# Table of Contents
* [Framing the Problem](#frame_problem)
    - [Business objective](#goal)
    - [Evaluation metric](#metric)
    - [Data description](#data_des)
* [Getting the Data](#getting_data)
* [Exploring the Data](#eda)
    - [Weather data](#weather)
    - [Merged data](#merged)
        - [Attributes characteristics](#info)
        - [Missing values](#missing)

## Framing the Problem
<a id="frame_problem"></a>

### Business Objective
<a id="goal"></a>

Significant investments are being made to improve building efficiencies to reduce costs and emissions. The question is, are the improvements working? Under pay-for-performance financing, the building owner makes payments based on the difference between their real energy consumption and what they would have used without any retrofits. The latter values have to come from a model. Current methods of estimation are fragmented and do not scale well. Some assume a specific meter type or don’t work with different building types.

The goal of this project is to come up with accurate models of metered building energy usage in the following areas: chilled water, electric, hot water, and steam meters. The data comes from over 1,000 buildings over a three-year timeframe. With better estimates of these energy-saving investments, large scale investors and financial institutions will be more inclined to invest in this area to enable progress in building efficiencies.

### Evaluation Metric
<a id="metric"></a>

The evaluation metric is Root Mean Squared Logarithmic Error. It is calculated as 

$\epsilon = \sqrt{\frac{1}{n}\sum^n_{i=1} \left(\log\left(p_i+1\right)-\log\left(a_i+1\right)\right)^2},$ 

where

* $n$ is the total number of observations in the (public/private) data set.
* $p_i$ is the prediction of target.
* $a_i$ is the actual target for $i$.

### Data Description
<a id="data_desc"></a>

Assessing the value of energy efficiency improvements can be challenging as there's no way to truly know how much energy a building would have used without the improvements. The best we can do is to build counterfactual models. Once a building is overhauled the new (lower) energy consumption is compared against modeled values for the original building to calculate the savings from the retrofit. More accurate models could support better market incentives and enable lower cost financing.

These counterfactual models will bi build across four energy types based on historic usage rates and observed weather. The dataset includes three years of hourly meter readings from over one thousand buildings at several different sites around the world.

**train.csv**
* `building_id` - Foreign key for the building metadata.
* `meter` - The meter id code. Read as `{0: electricity, 1: chilledwater, 2: steam, 3: hotwater}`. Not every building has all meter types.
* `timestamp`  - When the measurement was taken
* `meter_reading` - The target variable. Energy consumption in kWh (or equivalent). Note that this is real data with measurement error, which we expect will impose a baseline level of modeling error.

**building_meta.csv**
* `site_id` - Foreign key for the weather files.
* `building_id` - Foreign key for training.csv
* `primary_use` - Indicator of the primary category of activities for the building based on EnergyStar property type definitions
* `square_feet` - Gross floor area of the building
* `year_built` - Year building was opened
* `floor_count` - Number of floors of the building

**weather_[train/test].csv**

Weather data from a meteorological station as close as possible to the site.

* `site_id`
* `timestamp` - When the measurement was taken
* `air_temperature` - Degrees Celsius
* `cloud_coverage` - Portion of the sky covered in clouds, in oktas
* `dew_temperature` - Degrees Celsius
* `precip_depth_1_hr` - Millimeters
* `sea_level_pressure` - Millibar/hectopascals
* `wind_direction` - Compass direction (0-360)
* `wind_speed` - Meters per second

**test.csv**

The submission files use row numbers for ID codes in order to save space on the file uploads. test.csv has no feature data; it exists so you can get your predictions into the correct order.

* `row_id` - Row id for your submission file
* `building_id` - Building id code
* `meter` - The meter id code
* `timestamp` - Timestamps for the test data period

In [2]:
# Libraries

%load_ext autoreload
%autoreload 2

import os
import pandas as pd
import numpy as np
import datetime as dt
import gc
import missingno as msno
import pandas_profiling

from src.functions import data_import as dimp
from src.functions import data_exploration as dexp

#visualization
import matplotlib.pyplot as plt
import seaborn as sns
import plotly as pty

import plotly.graph_objs as go
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import cufflinks as cf
cf.set_config_file(offline=True)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Getting the data
<a id="getting_data"></a>

In [30]:
# location of files
TRAIN_RAW_DATA_LOC = '../data/raw/train/'

# Training data, separete imports
weather = dimp.import_data('../data/raw/train/weather_train.csv')
train = dimp.import_data('../data/raw/train/train.csv')
building_meta = dimp.import_data('../data/raw/train/building_metadata.csv')

# Creating a dataframe merging the separate datasets
df = dimp.import_raw_data(TRAIN_RAW_DATA_LOC)

Memory usage of dataframe is 9.60 MB
Memory usage after optimization is: 2.65 MB
Decreased by 72.4%


## Exploratory the data
<a id="eda"></a>

### Weather and train data
<a id="weather" />

In [50]:
weather[weather['site_id']==4].head()

site_id            timestamp  air_temperature  cloud_coverage  \
35110        4  2016-01-01 01:00:00         9.398438             0.0   
35111        4  2016-01-01 02:00:00         8.296875             0.0   
35112        4  2016-01-01 03:00:00         7.800781             0.0   
35113        4  2016-01-01 04:00:00         5.000000             0.0   
35114        4  2016-01-01 05:00:00         5.601562             0.0   

       dew_temperature  precip_depth_1_hr  sea_level_pressure  wind_direction  \
35110        -2.199219                0.0              1021.5           360.0   
35111        -2.800781                0.0              1021.5             0.0   
35112        -2.800781                0.0              1021.5            90.0   
35113        -0.600098                0.0              1022.0             0.0   
35114        -1.099609                0.0              1021.5           130.0   

       wind_speed  
35110    3.099609  
35111    0.000000  
35112    1.500000  
35113    0.000000  
35114    3.099609

In [34]:
train.head()

building_id  meter            timestamp  meter_reading
0            0      0  2016-01-01 00:00:00            0.0
1            1      0  2016-01-01 00:00:00            0.0
2            2      0  2016-01-01 00:00:00            0.0
3            3      0  2016-01-01 00:00:00            0.0
4            4      0  2016-01-01 00:00:00            0.0

In [37]:
merge1 = pd.merge(building_meta, train, how='left', on='building_id')

merge1.head()

site_id  building_id primary_use  square_feet  year_built  floor_count  \
0        0            0   Education         7432      2008.0          NaN   
1        0            0   Education         7432      2008.0          NaN   
2        0            0   Education         7432      2008.0          NaN   
3        0            0   Education         7432      2008.0          NaN   
4        0            0   Education         7432      2008.0          NaN   

   meter            timestamp  meter_reading  
0      0  2016-01-01 00:00:00            0.0  
1      0  2016-01-01 01:00:00            0.0  
2      0  2016-01-01 02:00:00            0.0  
3      0  2016-01-01 03:00:00            0.0  
4      0  2016-01-01 04:00:00            0.0

In [45]:
merge1[merge1['site_id']==1].head()

site_id  building_id primary_use  square_feet  year_built  \
1076662        1          105   Education        50623         NaN   
1076663        1          105   Education        50623         NaN   
1076664        1          105   Education        50623         NaN   
1076665        1          105   Education        50623         NaN   
1076666        1          105   Education        50623         NaN   

         floor_count  meter            timestamp  meter_reading  
1076662          5.0      0  2016-01-01 00:00:00      23.303600  
1076663          5.0      0  2016-01-01 01:00:00      45.607101  
1076664          5.0      0  2016-01-01 02:00:00      45.607101  
1076665          5.0      0  2016-01-01 03:00:00      45.107101  
1076666          5.0      0  2016-01-01 04:00:00      45.607101

In [53]:
weather_s4 = weather[weather['site_id']==4]
weather_s4['timestamp'] = pd.to_datetime(weather_s4['timestamp']) 

weather_s4.set_index('timestamp')[
    [
        'air_temperature',
        'cloud_coverage',
        'dew_temperature',
        'sea_level_pressure',
        'precip_depth_1_hr',
        'wind_direction',
        'wind_speed',
    ]
].iplot(kind='scatter', filename='cufflinks/cf-simple-line')

### Merged data
<a id="merged" />

#### Attributes characteristics
<a id="info"></a>

In [ ]:
# Dataset dimension
df.shape

In [ ]:
# Type of attributes
df.info()

In [ ]:
# Dataset sample
df.head()

In [ ]:
# Type of distribution for numerical attributes
%matplotlib inline
df.drop('timestamp', axis=1).hist(bins=50, figsize=(15,10))
plt.show()

#### Missing values
<a id="missing"></a>

In [ ]:
# Setting mutiple index for aggregation operations
df.set_index(['site_id','building_id','timestamp'], inplace=True)
df.head()

In [ ]:
# Percentage of missing values in each variable, grouped by site_id
dexp.get_missing_percentage(df,'site_id')

The only site with no completely missing columns is **site 4**, so **it'll be the selected site to perform a first full end-to-end analysis and modelling**.

In [ ]:
df.reset_index(inplace=True)
df.head()

In [ ]:
df_s4 = dimp.get_data_by_site(df, 4)

In [ ]:
df_s4.head()

In [ ]:
df_s4.info()